# Named Entity Recognition с нуля

## Зависимости

In [1]:
%%writefile requirements.txt
pytorch_lightning
numpy
pandas
scikit-learn
transformers
razdel == 0.5.0
ipymarkup == 0.9.0
slovnet == 0.5.0
natasha == 1.4.0
fasttext
deeppavlov

Writing requirements.txt


In [2]:
!pip install --upgrade -r requirements.txt

     |████████████████████████████████| 527 kB 21.0 MB/s 
     |████████████████████████████████| 3.8 MB 17.3 MB/s 
     |████████████████████████████████| 49 kB 6.5 MB/s 
     |████████████████████████████████| 34.4 MB 111 kB/s 
     |████████████████████████████████| 68 kB 8.1 MB/s 
     |████████████████████████████████| 880 kB 55.9 MB/s 
     |████████████████████████████████| 55 kB 4.6 MB/s 
     |████████████████████████████████| 41 kB 149 kB/s 
     |████████████████████████████████| 829 kB 66.1 MB/s 
     |████████████████████████████████| 397 kB 59.7 MB/s 
     |████████████████████████████████| 952 kB 60.2 MB/s 
     |████████████████████████████████| 596 kB 61.4 MB/s 
     |████████████████████████████████| 134 kB 72.4 MB/s 
     |████████████████████████████████| 1.1 MB 56.1 MB/s 
     |████████████████████████████████| 895 kB 55.6 MB/s 
     |████████████████████████████████| 67 kB 6.8 MB/s 
     |████████████████████████████████| 6.5 MB 53.7 MB/s 
  Using cached pybind11-

## Датасет
Новый день - новый датасет!

In [1]:
!rm -f Persons-1000.zip
!wget -q http://ai-center.botik.ru/Airec/ai-resources/Persons-1000.zip
!unzip -qq Persons-1000.zip

In [2]:
!cat Persons-1000/collection/001/anno.markup.xml  

﻿<markup>
<entry>
<id>1</id>
<offset>308</offset>
<length>16</length>
<class>AAA_Estimate_Person</class>
<attribute>
<name>Canonical</name>
<value>ГРИГОРИЙ КАРАСИН</value>
</attribute>
</entry>
<entry>
<id>2</id>
<offset>387</offset>
<length>15</length>
<class>AAA_Estimate_Person</class>
<attribute>
<name>Canonical</name>
<value>ДЭНИЭЛ ФРИД</value>
</attribute>
</entry>
</markup>


Named Entity Recognition - распознавание именных сущностей. Выделяем в тексте спаны PER, LOC, ORG.

В случае с Persons-1000 только PER. Считаем датасет из XML.

In [3]:
import os
import xml.etree.ElementTree as ET
from ipymarkup import show_box_markup
from ipymarkup.palette import palette, BLUE, RED, GREEN

directory = "Persons-1000/collection/"

def read_text_with_markup(directory):
    MARKUP_FILE_NAME = "anno.markup.xml"
    TEXT_FILE_NAME = "text.txt"
    ENCODING = "windows-1251"
    ENTRY_TAG = "entry"
    START_POS_TAG = "offset"
    LENGTH_TAG = "length"

    markup_file_name = os.path.join(directory, MARKUP_FILE_NAME)
    text_file_name = os.path.join(directory, TEXT_FILE_NAME)
    with open(text_file_name, "r", encoding=ENCODING) as r:
        text = r.read()
    text = text.replace("\n", "\r\n")
    
    root = ET.parse(markup_file_name).getroot()
    spans = []
    for entry in root.findall(ENTRY_TAG):
        start_pos = int(entry.find(START_POS_TAG).text)
        end_pos = start_pos + int(entry.find(LENGTH_TAG).text)
        spans.append((start_pos, end_pos, "PER"))
    return text, spans

data = []
for sample_name in os.listdir(directory):
    sample_path = os.path.join(directory, sample_name)
    data.append(read_text_with_markup(sample_path))

ipymarkup - модуль для вывода NER разметки в ipynb

In [4]:
data[0]

('Мэр Москвы Сергей Собянин подписал распоряжение об увольнении заместителя префекта Центрального административного округа (ЦАО) Москвы Леонида Сидорова, сообщил РИА Новости в четверг источник в городской администрации. "Своим распоряжением от 17 ноября мэр Москвы Сергей Собянин освободил Леонида Сидорова от замещаемой должности заместителя префекта ЦАО Москвы и уволил с государственной гражданской службы города по собственной инициативе", - сказал собеседник агентства.\r\n\r\nКроме того, по его словам, Собянин назначил руководителем аппарата префектуры Северного административного округа Москвы в ранге заместителя префекта Ольгу Устимову.\r\n\r\n"Устимова назначена с заключением служебного контракта сроком на четыре года", - добавил он.\r\n\r\nРанее префектом ЦАО был назначен Сергей Байдаков, который с октября 2008 года занимал должность заместителя мэра столицы по вопросам физкультуры, спорта и межрегионального сотрудничества. С декабря 2003 года по октябрь 2008 года Байдаков уже был 

In [5]:
data[0][1]

[(11, 25, 'PER'),
 (134, 150, 'PER'),
 (263, 277, 'PER'),
 (288, 304, 'PER'),
 (503, 510, 'PER'),
 (625, 639, 'PER'),
 (645, 653, 'PER'),
 (773, 788, 'PER'),
 (969, 977, 'PER')]

In [6]:
show_box_markup(data[0][0], data[0][1], palette=palette(PER=BLUE, ORG=RED, LOC=GREEN))

## BIO

BIO разметка: B - begin, I - inner, O - outer. Преобразуем задачу разметки спанов в задачу классификации каждого слова.

0 = O = outer, 1 = B = begin, 2 = I = inner

In [7]:
from enum import IntEnum
from collections import namedtuple

from razdel import tokenize

class Label(IntEnum):
    OUTER = 0
    BEGIN = 1
    INNER = 2

Sample = namedtuple("Sample", "text,tokens,spans,labels")

def text_span_to_sample(text, spans):
    labels = []
    tokens = list(tokenize(text))
    for token in tokens:
        label = Label.OUTER
        for span in spans:
            # Начало или часть какого-то спана
            # Не совсем корректно из-за возможных различий разметки и токенизации
            span_begin, span_end, tag = span
            if token.start == span_begin:
                label = Label.BEGIN
            elif token.start > span_begin and token.stop <= span_end:
                label = Label.INNER
        labels.append(label)
    # Проверяем инвариант отсутствия последовательных пар (0, 2)
    assert len([1 for i in range(len(labels) - 1) if (labels[i], labels[i+1]) == (0, 2)]) == 0
    return Sample(text, tokens, spans, labels)

samples = []
for text, spans in data:
    samples.append(text_span_to_sample(text, spans))

show_box_markup(samples[0].text, samples[0].spans, palette=palette(PER=BLUE, ORG=RED, LOC=GREEN))
print(samples[0].labels)
print(len(samples))

[<Label.OUTER: 0>, <Label.OUTER: 0>, <Label.BEGIN: 1>, <Label.INNER: 2>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.BEGIN: 1>, <Label.INNER: 2>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.BEGIN: 1>, <Label.INNER: 2>, <Label.OUTER: 0>, <Label.BEGIN: 1>, <Label.INNER: 2>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OUTER: 0>, <Label.OU

In [8]:
samples[0].labels[:10]

[<Label.OUTER: 0>,
 <Label.OUTER: 0>,
 <Label.BEGIN: 1>,
 <Label.INNER: 2>,
 <Label.OUTER: 0>,
 <Label.OUTER: 0>,
 <Label.OUTER: 0>,
 <Label.OUTER: 0>,
 <Label.OUTER: 0>,
 <Label.OUTER: 0>]

In [9]:
samples[0].labels[:10]

[<Label.OUTER: 0>,
 <Label.OUTER: 0>,
 <Label.BEGIN: 1>,
 <Label.INNER: 2>,
 <Label.OUTER: 0>,
 <Label.OUTER: 0>,
 <Label.OUTER: 0>,
 <Label.OUTER: 0>,
 <Label.OUTER: 0>,
 <Label.OUTER: 0>]

Бьём на выборки

In [10]:
import random
random.shuffle(samples)

train = samples[:700]
val = samples[700:850]
test = samples[850:]

In [11]:
train[0]

Sample(text='Владимир Путин огласил состав правительства\r\n\r\nПрезидент России Владимир Путин огласил состав нового правительства, которое возглавляет бывший глава государства Дмитрий Медведев. У Медведева будет шесть простых заместителей. Новыми вице-премьерами стали его бывший помощник Аркадий Дворкович и Ольга Голодец, пришедшая из мэрии Москвы.\r\n\r\nСвои посты замов сохранили Дмитрий Козак, Владислав Сурков (теперь он глава аппарата правительства), Дмитрий Рогозин и Александр Хлопонин. Пост первого вице-премьера остался за Игорем Шуваловым.\r\n\r\nТаким образом, из вице-премьеров ушел Игорь Сечин, курировавший ТЭК. Поста первого вице-премьера лишился Виктор Зубков.\r\n\r\nРашиду Нургалиеву не досталось поста в правительстве. МВД возглавил Владимир Колокольцев, руководивший московской полицией. Министерство культуры от Александра Авдеева перешло к Владимиру Мединскому, бывшему депутату Госдумы от "Единой России". Министр образования Андрей Фурсенко также не удержался на посту. Е

In [12]:
len(test)

150

In [13]:
len(data)

1000

In [14]:
char_set = ["<pad>", "<unk>"] + list({ch for sample in train for token in sample.tokens for ch in token.text})
print(char_set)

['<pad>', '<unk>', '+', 'a', 'x', 'Q', '!', 'j', 'у', 'C', 'b', 'М', '(', '9', 'h', 'I', 'M', 'v', 'Ы', '#', 'Р', 'Х', 'щ', 'G', 'я', 'э', 'й', 't', 'з', '"', '>', 'L', 'Д', 'Й', 'в', 'Ф', 'r', '[', 'о', 'V', 'k', '—', '&', '.', ']', 'P', 'Щ', 'N', 'с', 'T', 'Е', ')', '•', '»', 'e', '1', 'Б', 'Ё', '\xad', 'J', ';', 'Ж', 'Н', '2', 'З', 'o', '|', 'р', '©', 'A', 'Ю', 'Z', '3', 'q', '“', 'х', 'ю', 'И', 'm', 'ё', '8', 'і', "'", 'ш', 'м', 'X', 'и', 'е', 'l', 'f', 'Ч', '«', 'g', 'ж', 'S', 'ы', 'к', 'Ш', '%', '”', '-', 'С', '6', 'W', 'p', 'u', 'd', '$', 'E', 'К', 'В', 'y', 'п', 'а', 'c', 'H', '0', '№', 'н', 'А', 'z', 'Я', 'n', 'Э', 'U', 'ь', 'w', 'F', 'т', 'Г', 'ц', 'B', 'K', 'Ц', 'Т', '4', ':', 'O', 'R', 'i', '€', 'б', 'ф', '<', 'Ъ', '?', 'Л', 'О', 's', 'д', '…', '/', 'П', '5', 'D', '7', 'Ь', 'Y', '–', 'л', ',', 'ъ', 'г', 'У', 'ч']


Для каждого слова сохраняем его символьный состав, а в остальном старый добрый пайплайн

In [15]:
import torch
from torch.utils.data import Dataset
from torch.utils.data import DataLoader, RandomSampler

class NerCharsDataset(Dataset):
    def __init__(self, samples, char_set, max_seq_len=500, max_char_seq_len=50):
        assert len(samples) != 0
        self.samples = []
        self.tokens = []
        self.texts = []
        for sample in samples:
            inputs = torch.zeros((max_seq_len, max_char_seq_len), dtype=torch.long)
            for token_num, token in enumerate(sample.tokens[:max_seq_len]):
                for ch_num, ch in enumerate(token.text[:max_char_seq_len]):
                    char_index = char_set.index(ch) if ch in char_set else char_set.index("<unk>")
                    inputs[token_num][ch_num] = char_index
            labels = torch.zeros((max_seq_len,), dtype=torch.long)
            input_labels = [int(i) for i in sample.labels[:max_seq_len]]
            labels[:len(input_labels)] = torch.LongTensor(input_labels)
            self.samples.append((torch.LongTensor(inputs), torch.LongTensor(labels)))
            self.tokens.append(sample.tokens[:max_seq_len])
            self.texts.append(sample.text)
    
    def __len__(self):
        return len(self.samples)
    
    def __getitem__(self, index):
        return self.samples[index]

    def get_tokens(self, index):
        return self.tokens[index]
    
    def get_text(self, index):
        return self.texts[index]


BATCH_SIZE = 32

train_data = NerCharsDataset(train, char_set)
train_sampler = RandomSampler(train_data)
train_loader = DataLoader(train_data, batch_size=BATCH_SIZE, sampler=train_sampler)

val_data = NerCharsDataset(val, char_set)
val_loader = DataLoader(val_data, batch_size=BATCH_SIZE)

test_data = NerCharsDataset(test, char_set)
test_loader = DataLoader(test_data, batch_size=BATCH_SIZE)

In [16]:
for sample in train_loader:
    inputs, labels = sample
    print(inputs.size())
    print(labels.size())
    break

# inputs: batch_size x num_words x num_chars
# labels: batch_size x num_words

torch.Size([32, 500, 50])
torch.Size([32, 500])


In [17]:
import torch
import torch.nn as nn
from pytorch_lightning import LightningModule
from torchmetrics import Accuracy
 

class TemplateModel(LightningModule):
    def __init__(self):
        super().__init__()
        
        self.loss = nn.CrossEntropyLoss()
        self.valid_accuracy = Accuracy()
        self.test_accuracy = Accuracy()
    
    def forward(self, inputs, labels):
        raise NotImplementedError("forward not implemented")
    
    def configure_optimizers(self):
        optimizer = torch.optim.Adam(self.parameters(), lr=1e-3)
        return [optimizer]
    
    def training_step(self, batch, _):
        inputs, labels = batch
        loss, logits = self(inputs, labels)
        return loss
    
    def validation_step(self, batch, _):
        inputs, labels = batch
        val_loss, logits = self(inputs, labels)
        self.valid_accuracy.update(logits, labels)
        self.log("val_loss", val_loss, prog_bar=True)
        self.log("val_acc", self.valid_accuracy)

    def validation_epoch_end(self, outs):
        self.log("val_acc_epoch", self.valid_accuracy.compute(), prog_bar=True)

    def test_step(self, batch, _):
        inputs, labels = batch
        test_loss, logits = self(inputs, labels)
        self.test_accuracy.update(logits, labels)
        self.log("test_loss", test_loss, prog_bar=True)
        self.log("test_acc", self.test_accuracy)

    def test_epoch_end(self, outs):
        self.log("test_acc_epoch", self.test_accuracy.compute(), prog_bar=True)

## Бесконтекстная модель

In [18]:
import torch
from torch import nn
from pytorch_lightning import Trainer
from pytorch_lightning.callbacks import EarlyStopping

class SuperSimpleModel(TemplateModel):
    def __init__(self, char_set_size, char_embedding_dim=32, classes_count=3, char_max_seq_len=50):
        super().__init__()
        
        self.embeddings_layer = nn.Embedding(char_set_size, char_embedding_dim) # а -> [0.1, ... 0.3]
        self.out_layer = nn.Linear(char_max_seq_len * char_embedding_dim, classes_count)

    def forward(self, inputs, labels):
        projections = self.embeddings_layer.forward(inputs)
        projections = projections.reshape(projections.size(0), projections.size(1), -1) # <-
        logits = self.out_layer.forward(projections)
        logits = logits.transpose(1, 2)
        loss = self.loss(logits, labels)
        return loss, logits


super_simple_model = SuperSimpleModel(len(char_set))
early_stop_callback = EarlyStopping(
    monitor="val_loss",
    min_delta=0.0,
    patience=5,
    verbose=True,
    mode="min" 
)
trainer = Trainer(
    gpus=1,
    checkpoint_callback=False,
    accumulate_grad_batches=1,
    max_epochs=150,
    progress_bar_refresh_rate=10,
    callbacks=[early_stop_callback])
trainer.fit(super_simple_model, train_loader, val_loader)
trainer.test(super_simple_model, test_loader)

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/callback_connector.py:148: LightningDeprecationWarning: Setting `Trainer(checkpoint_callback=False)` is deprecated in v1.5 and will be removed in v1.7. Please consider using `Trainer(enable_checkpointing=False)`.
  f"Setting `Trainer(checkpoint_callback={checkpoint_callback})` is deprecated in v1.5 and will "
/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/callback_connector.py:91: LightningDeprecationWarning: Setting `Trainer(progress_bar_refresh_rate=10)` is deprecated in v1.5 and will be removed in v1.7. Please pass `pytorch_lightning.callbacks.progress.TQDMProgressBar` with `refresh_rate` directly to the Trainer's `callbacks` argument instead. Or, to disable the progress bar pass `enable_progress_bar = False` to the Trainer.
  f"Setting `Trainer(progress_bar_refresh_rate={progress_bar_refresh_rate})` is deprecated in v1.5 and"
GPU available: True, used: True
TPU available: False,

Validation sanity check: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/data_loading.py:433: UserWarning: The number of training samples (22) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.
  f"The number of training samples ({self.num_training_batches}) is smaller than the logging interval"


Training: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

...

Validating: 0it [00:00, ?it/s]

Monitored metric val_loss did not improve in the last 5 records. Best score: 0.065. Signaling Trainer to stop.
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.9763466715812683,
 'test_acc_epoch': 0.9763466715812683,
 'test_loss': 0.06498317420482635}
--------------------------------------------------------------------------------


[{'test_acc': 0.9763466715812683,
  'test_acc_epoch': 0.9763466715812683,
  'test_loss': 0.06498317420482635}]

## Метрики

Можно использовать как классические мультиклассификационнные метрики, так и метрики специально для NER.

Например, число точных и частичных совпадений спанов, пропущенных и лишних спанов.

In [19]:
def get_spans(labels, tokens):
    spans = []
    for i, (label, token) in enumerate(zip(labels, tokens)):
        if label == 1:
            spans.append((token.start, token.stop, "PER"))
        elif label == 2:
            assert len(spans) != 0, "Incorrect label sequence: {}".format(labels)
            old_begin, _, old_tag = spans[-1]
            spans[-1] = (old_begin, token.stop, old_tag)
    return spans


def compare_span_sets(left_spans, right_spans):
    exact, partial, missing = 0, 0, 0
    for left_span in left_spans:
        is_missing = True
        for right_span in right_spans:
            if left_span == right_span:
                exact += 1
                is_missing = False
                break
            ls, le, _ = left_span
            rs, re, _ = right_span
            # [ls le] [rs re]
            # [rs re] [ls le]
            if not (ls <= le <= rs <= re or rs <= re <= ls <= le):
                is_missing = False
                partial += 1
                break            
        if is_missing:
            missing += 1
    return exact, partial, missing


def calc_metrics(true_labels, predicted_labels, tokens):
    # Метрики классификации
    one_tp, one_fp, one_fn = 0, 0, 0
    for true, predicted in zip(true_labels, predicted_labels):
        for l1, l2 in zip(true, predicted):
            if l1 == 1 and l2 == 1:
                one_tp += 1
            elif l1 != 1 and l2 == 1:
                one_fp += 1
            elif l1 == 1 and l2 !=1:
                one_fn += 1
    if one_tp + one_fp == 0:
        print("No positives!")
    else:
        print("1 Precision: {}, 1 Recall: {}".format(float(one_tp)/(one_tp + one_fp), float(one_tp)/(one_tp + one_fn)))

    # Специализированные метрики
    e, p, m, s = 0, 0, 0, 0
    for (true, predicted), sample_tokens in zip(zip(true_labels, predicted_labels), tokens):
        true_spans = get_spans(true, sample_tokens)
        predicted_spans = get_spans(predicted, sample_tokens)
        exact, partial, missing = compare_span_sets(true_spans, predicted_spans)
        _, _, spurius = compare_span_sets(predicted_spans, true_spans)
        e += exact
        p += partial
        m += missing
        s += spurius
    print("Exact: {}, partial: {}, missing: {}, spurius: {}".format(e, p, m, s))
            


def predict(model, test_loader, show_sample_index=51):
    device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
    model.to(device)
    model.eval()
    all_true_labels, all_predicted_labels, all_tokens, all_texts = [], [], [], []
    for batch_index, batch in enumerate(test_loader):
        inputs, true_labels = batch
        batch_size = inputs.size(0)
        _, logits = model(inputs.to(device), true_labels.to(device))
        predicted_labels = logits.max(dim=1)[1].detach().cpu()

        # Убираем неконсистентность BIO
        for sample_num, sample in enumerate(predicted_labels):
            for token_num, label in enumerate(sample):
                if token_num == 0 and label == 2:
                    predicted_labels[sample_num][0] = 1
                    continue
                prev_label = sample[token_num - 1]
                if label == 2 and prev_label == 0:
                    predicted_labels[sample_num][token_num] = 1

        all_true_labels.extend(true_labels)
        all_predicted_labels.extend(predicted_labels)
        for i in range(batch_size):
            all_tokens.append(test_data.get_tokens(batch_index * batch_size + i))
            all_texts.append(test_data.get_text(batch_index * batch_size + i))

    calc_metrics(all_true_labels, all_predicted_labels, all_tokens)
    print("PREDICTED:")
    show_box_markup(all_texts[show_sample_index],
                    get_spans(all_predicted_labels[show_sample_index], all_tokens[show_sample_index]),
                    palette=palette(PER=BLUE, ORG=RED, LOC=GREEN))

In [20]:
predict(super_simple_model, test_loader)

1 Precision: 0.610041265474553, 1 Recall: 0.634024303073624
Exact: 483, partial: 578, missing: 288, spurius: 178
PREDICTED:


## Контекстная модель: LSTM над конкатенацией

In [21]:
import torch
from torch import nn
from pytorch_lightning import Trainer
from pytorch_lightning.callbacks import EarlyStopping

class LstmModel(TemplateModel):
    def __init__(self, char_set_size, char_embedding_dim=4, classes_count=3,
                 lstm_embedding_dim=8, char_max_seq_len=50):
        super().__init__()
        
        self.embeddings_layer = nn.Embedding(char_set_size, char_embedding_dim)
        self.dropout = nn.Dropout(0.4)
        self.lstm_layer = nn.LSTM(char_embedding_dim * char_max_seq_len, lstm_embedding_dim // 2,
                                  batch_first=True, bidirectional=True)
        self.out_layer = nn.Linear(lstm_embedding_dim, classes_count)

    def forward(self, inputs, labels):
        batch_size = inputs.size(0)
        seq_len = inputs.size(1)
        projections = self.embeddings_layer.forward(inputs)
        projections = projections.reshape(projections.size(0), projections.size(1), -1)
        output, _= self.lstm_layer(projections)
        output = self.dropout(output)
        logits = self.out_layer.forward(output)
        logits = logits.transpose(1, 2)
        loss = self.loss(logits, labels)
        return loss, logits


lstm_model = LstmModel(len(char_set))
early_stop_callback = EarlyStopping(
    monitor="val_loss",
    min_delta=0.0,
    patience=5,
    verbose=True,
    mode="min" 
)
trainer = Trainer(
    gpus=1,
    checkpoint_callback=False,
    accumulate_grad_batches=1,
    max_epochs=200,
    progress_bar_refresh_rate=10,
    callbacks=[early_stop_callback])
trainer.fit(lstm_model, train_loader, val_loader)
trainer.test(lstm_model, test_loader)

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/callback_connector.py:148: LightningDeprecationWarning: Setting `Trainer(checkpoint_callback=False)` is deprecated in v1.5 and will be removed in v1.7. Please consider using `Trainer(enable_checkpointing=False)`.
  f"Setting `Trainer(checkpoint_callback={checkpoint_callback})` is deprecated in v1.5 and will "
/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/callback_connector.py:91: LightningDeprecationWarning: Setting `Trainer(progress_bar_refresh_rate=10)` is deprecated in v1.5 and will be removed in v1.7. Please pass `pytorch_lightning.callbacks.progress.TQDMProgressBar` with `refresh_rate` directly to the Trainer's `callbacks` argument instead. Or, to disable the progress bar pass `enable_progress_bar = False` to the Trainer.
  f"Setting `Trainer(progress_bar_refresh_rate={progress_bar_refresh_rate})` is deprecated in v1.5 and"
GPU available: True, used: True
TPU available: False,

Validation sanity check: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/data_loading.py:433: UserWarning: The number of training samples (22) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.
  f"The number of training samples ({self.num_training_batches}) is smaller than the logging interval"


Training: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

...

Validating: 0it [00:00, ?it/s]

Metric val_loss improved by 0.000 >= min_delta = 0.0. New best score: 0.060
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.9795200228691101,
 'test_acc_epoch': 0.9795200228691101,
 'test_loss': 0.0575537346303463}
--------------------------------------------------------------------------------


[{'test_acc': 0.9795200228691101,
  'test_acc_epoch': 0.9795200228691101,
  'test_loss': 0.0575537346303463}]

In [22]:
predict(lstm_model, test_loader)

1 Precision: 0.6188707280832095, 1 Recall: 0.5954253037884203
Exact: 581, partial: 480, missing: 288, spurius: 155
PREDICTED:


## Контекстная модель: LSTM над CharFF

In [23]:
import torch
from torch import nn
from pytorch_lightning import Trainer
from pytorch_lightning.callbacks import EarlyStopping

class CharFFLstmModel(TemplateModel):
    def __init__(self, char_set_size, char_embedding_dim=4, classes_count=3,
                 word_embedding_dim=16, lstm_embedding_dim=16, char_max_seq_len=50):
        super().__init__()
        
        self.embeddings_layer = nn.Embedding(char_set_size, char_embedding_dim)
        self.dropout = nn.Dropout(0.3)
        self.linear = nn.Linear(char_embedding_dim * char_max_seq_len, word_embedding_dim)
        self.relu = nn.ReLU()
        self.lstm_layer = nn.LSTM(word_embedding_dim, lstm_embedding_dim // 2, batch_first=True, bidirectional=True)
        self.out_layer = nn.Linear(lstm_embedding_dim, classes_count)

    def forward(self, inputs, labels):
        projections = self.embeddings_layer.forward(inputs)
        projections = projections.reshape(projections.size(0), projections.size(1), -1)
        projections = self.relu(self.linear(projections))
        projections = self.dropout(projections)
        output, _= self.lstm_layer(projections)
        output = self.dropout(output)
        logits = self.out_layer.forward(output)
        logits = logits.transpose(1, 2)
        loss = self.loss(logits, labels)
        return loss, logits


char_ff_lstm_model = CharFFLstmModel(len(char_set))
early_stop_callback = EarlyStopping(
    monitor="val_loss",
    min_delta=0.0,
    patience=8,
    verbose=True,
    mode="min" 
)
trainer = Trainer(
    gpus=1,
    checkpoint_callback=False,
    accumulate_grad_batches=1,
    max_epochs=150,
    progress_bar_refresh_rate=10,
    callbacks=[early_stop_callback])
trainer.fit(char_ff_lstm_model, train_loader, val_loader)
trainer.test(char_ff_lstm_model, test_loader)

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/callback_connector.py:148: LightningDeprecationWarning: Setting `Trainer(checkpoint_callback=False)` is deprecated in v1.5 and will be removed in v1.7. Please consider using `Trainer(enable_checkpointing=False)`.
  f"Setting `Trainer(checkpoint_callback={checkpoint_callback})` is deprecated in v1.5 and will "
/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/callback_connector.py:91: LightningDeprecationWarning: Setting `Trainer(progress_bar_refresh_rate=10)` is deprecated in v1.5 and will be removed in v1.7. Please pass `pytorch_lightning.callbacks.progress.TQDMProgressBar` with `refresh_rate` directly to the Trainer's `callbacks` argument instead. Or, to disable the progress bar pass `enable_progress_bar = False` to the Trainer.
  f"Setting `Trainer(progress_bar_refresh_rate={progress_bar_refresh_rate})` is deprecated in v1.5 and"
GPU available: True, used: True
TPU available: False,

Validation sanity check: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/data_loading.py:433: UserWarning: The number of training samples (22) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.
  f"The number of training samples ({self.num_training_batches}) is smaller than the logging interval"


Training: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

...

Validating: 0it [00:00, ?it/s]

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.9874399900436401,
 'test_acc_epoch': 0.9874399900436401,
 'test_loss': 0.03560539335012436}
--------------------------------------------------------------------------------


[{'test_acc': 0.9874399900436401,
  'test_acc_epoch': 0.9874399900436401,
  'test_loss': 0.03560539335012436}]

In [24]:
predict(char_ff_lstm_model, test_loader)

1 Precision: 0.7919413919413919, 1 Recall: 0.7726947819871337
Exact: 945, partial: 179, missing: 225, spurius: 169
PREDICTED:


## Задание 1.1
Сделайте то же самое, но с bidirectional LSTM на уровне символов

In [25]:
import torch
from torch import nn
from pytorch_lightning import Trainer
from pytorch_lightning.callbacks import EarlyStopping

class CharLstmModel(TemplateModel):
    def __init__(self, char_set_size, char_embedding_dim=4, classes_count=3,
                 lstm_embedding_dim=16, char_max_seq_len=50):
        super().__init__()
        
        self.embeddings_layer = nn.Embedding(char_set_size, char_embedding_dim)
        self.dropout = nn.Dropout(0.3)
        self.lstm_layer = nn.LSTM(char_embedding_dim, lstm_embedding_dim // 2, batch_first=True, bidirectional=True)
        self.out_layer = nn.Linear(lstm_embedding_dim * char_max_seq_len, classes_count)

    def forward(self, inputs, labels):
        projections = self.embeddings_layer.forward(inputs)
        char_max_seq_len = projections.size(2)
        projections = projections.reshape(projections.size(0), -1, projections.size(3))
        output, _= self.lstm_layer(projections)
        output = self.dropout(output)
        output = output.reshape(output.size(0), -1, output.size(2)*char_max_seq_len)
        logits = self.out_layer.forward(output)
        logits = logits.transpose(1, 2)
        loss = self.loss(logits, labels)
        return loss, logits


char_lstm_model = CharLstmModel(len(char_set))
early_stop_callback = EarlyStopping(
    monitor="val_loss",
    min_delta=0.0,
    patience=8,
    verbose=True,
    mode="min" 
)
trainer = Trainer(
    gpus=1,
    checkpoint_callback=False,
    accumulate_grad_batches=1,
    max_epochs=150,
    progress_bar_refresh_rate=10,
    callbacks=[early_stop_callback])
trainer.fit(char_lstm_model, train_loader, val_loader)
trainer.test(char_lstm_model, test_loader)

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/callback_connector.py:148: LightningDeprecationWarning: Setting `Trainer(checkpoint_callback=False)` is deprecated in v1.5 and will be removed in v1.7. Please consider using `Trainer(enable_checkpointing=False)`.
  f"Setting `Trainer(checkpoint_callback={checkpoint_callback})` is deprecated in v1.5 and will "
/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/callback_connector.py:91: LightningDeprecationWarning: Setting `Trainer(progress_bar_refresh_rate=10)` is deprecated in v1.5 and will be removed in v1.7. Please pass `pytorch_lightning.callbacks.progress.TQDMProgressBar` with `refresh_rate` directly to the Trainer's `callbacks` argument instead. Or, to disable the progress bar pass `enable_progress_bar = False` to the Trainer.
  f"Setting `Trainer(progress_bar_refresh_rate={progress_bar_refresh_rate})` is deprecated in v1.5 and"
GPU available: True, used: True
TPU available: False,

Validation sanity check: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/data_loading.py:433: UserWarning: The number of training samples (22) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.
  f"The number of training samples ({self.num_training_batches}) is smaller than the logging interval"


Training: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

...

Validating: 0it [00:00, ?it/s]

Monitored metric val_loss did not improve in the last 8 records. Best score: 0.049. Signaling Trainer to stop.
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.9738399982452393,
 'test_acc_epoch': 0.9738399982452393,
 'test_loss': 0.07061327248811722}
--------------------------------------------------------------------------------


[{'test_acc': 0.9738399982452393,
  'test_acc_epoch': 0.9738399982452393,
  'test_loss': 0.07061327248811722}]

In [26]:
predict(char_lstm_model, test_loader)

1 Precision: 0.5902872777017784, 1 Recall: 0.6168691922802001
Exact: 446, partial: 557, missing: 346, spurius: 323
PREDICTED:


## Задание 1.2
Сделайте то же самое, но со свёртками на уровне символов

In [27]:
import torch
import torch.nn as nn
from pytorch_lightning import Trainer
from pytorch_lightning.callbacks import EarlyStopping  

class CharCNNModel(TemplateModel):
    def __init__(self, char_set_size, char_embedding_dim=4, classes_count=3,
                 kernel_size=5, channels=500, char_max_seq_len=50):
        super().__init__()
        
        self.embedding = nn.Embedding(char_set_size, char_embedding_dim)
        self.cnn = nn.Conv1d(in_channels=channels, out_channels=channels, kernel_size=char_embedding_dim*kernel_size)
        self.relu = nn.ReLU()
        self.dropout = nn.Dropout(0.2)
        self.out_layer = nn.Linear(char_embedding_dim*char_max_seq_len - (char_embedding_dim*kernel_size - 1), classes_count)
    
    def forward(self, inputs, labels):
        projections = self.embedding.forward(inputs)
        projections = projections.reshape(projections.size(0), projections.size(1), -1)
        convolved = self.dropout(self.relu(self.cnn(projections)))
        logits = self.out_layer.forward(convolved)
        
        logits = logits.transpose(1, 2)
        loss = self.loss(logits, labels)
        return loss, logits

char_cnn_model = CharCNNModel(len(char_set))
early_stop_callback = EarlyStopping(
    monitor="val_loss",
    min_delta=0.0,
    patience=8,
    verbose=True,
    mode="min" 
)
trainer = Trainer(
    gpus=1,
    checkpoint_callback=False,
    accumulate_grad_batches=1,
    max_epochs=150,
    progress_bar_refresh_rate=10,
    callbacks=[early_stop_callback])
trainer.fit(char_cnn_model, train_loader, val_loader)
trainer.test(char_cnn_model, test_loader)

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/callback_connector.py:148: LightningDeprecationWarning: Setting `Trainer(checkpoint_callback=False)` is deprecated in v1.5 and will be removed in v1.7. Please consider using `Trainer(enable_checkpointing=False)`.
  f"Setting `Trainer(checkpoint_callback={checkpoint_callback})` is deprecated in v1.5 and will "
/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/callback_connector.py:91: LightningDeprecationWarning: Setting `Trainer(progress_bar_refresh_rate=10)` is deprecated in v1.5 and will be removed in v1.7. Please pass `pytorch_lightning.callbacks.progress.TQDMProgressBar` with `refresh_rate` directly to the Trainer's `callbacks` argument instead. Or, to disable the progress bar pass `enable_progress_bar = False` to the Trainer.
  f"Setting `Trainer(progress_bar_refresh_rate={progress_bar_refresh_rate})` is deprecated in v1.5 and"
GPU available: True, used: True
TPU available: False,

Validation sanity check: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/data_loading.py:433: UserWarning: The number of training samples (22) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.
  f"The number of training samples ({self.num_training_batches}) is smaller than the logging interval"


Training: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

...

Validating: 0it [00:00, ?it/s]

Monitored metric val_loss did not improve in the last 8 records. Best score: 0.243. Signaling Trainer to stop.
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.9614666700363159,
 'test_acc_epoch': 0.9614666700363159,
 'test_loss': 0.26895689964294434}
--------------------------------------------------------------------------------


[{'test_acc': 0.9614666700363159,
  'test_acc_epoch': 0.9614666700363159,
  'test_loss': 0.26895689964294434}]

In [28]:
predict(char_cnn_model, test_loader)

1 Precision: 0.017543859649122806, 1 Recall: 0.0007147962830593281
Exact: 0, partial: 9, missing: 1340, spurius: 48
PREDICTED:


## Задание 1.3
Сделайте то же самое, но с CRF над головой

## Задание 2*
Сделайте то же самое, но с XLMRobertaForTokenClassification. Не забудьте про word -> subwords!

In [29]:
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("xlm-roberta-base")
for sample in train:
    for token, label in zip(sample.tokens, sample.labels):
        input_ids = tokenizer(token.text, add_special_tokens=False)["input_ids"]
        print(token.text, tokenizer.tokenize(token.text), input_ids)
    break

/usr/local/lib/python3.7/dist-packages/cryptography/hazmat/backends/openssl/x509.py:17: CryptographyDeprecationWarning: This version of cryptography contains a temporary pyOpenSSL fallback path. Upgrade pyOpenSSL now.
  utils.DeprecatedIn35,


Downloading:   0%|          | 0.00/615 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/4.83M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/8.68M [00:00<?, ?B/s]

Владимир ['▁Владимир'] [21996]
Путин ['▁Путин'] [27910]
огласил ['▁оглас', 'ил'] [128740, 3873]
состав ['▁состав'] [27135]
правительства ['▁правительства'] [128530]
Президент ['▁Президент'] [20224]
России ['▁России'] [8568]
Владимир ['▁Владимир'] [21996]
Путин ['▁Путин'] [27910]
огласил ['▁оглас', 'ил'] [128740, 3873]
состав ['▁состав'] [27135]
нового ['▁нового'] [33372]
правительства ['▁правительства'] [128530]
, ['▁', ','] [6, 4]
которое ['▁которое'] [27390]
возглавляет ['▁воз', 'глав', 'ляет'] [11125, 38664, 87646]
бывший ['▁бы', 'вший'] [2294, 64393]
глава ['▁глава'] [41976]
государства ['▁государства'] [51452]
Дмитрий ['▁Дмитрий'] [154888]
Медведев ['▁Медведев'] [189322]
. ['▁', '.'] [6, 5]
У ['▁У'] [447]
Медведева ['▁Медведев', 'а'] [189322, 59]
будет ['▁будет'] [3318]
шесть ['▁шесть'] [171792]
простых ['▁простых'] [226444]
заместителей ['▁', 'заместител', 'ей'] [6, 208150, 2519]
. ['▁', '.'] [6, 5]
Новыми ['▁Новы', 'ми'] [87430, 827]
вице-премьерами ['▁вице', '-', 'премьер', 'ам

# NER из коробки

https://github.com/natasha/natasha

https://github.com/deepmipt/DeepPavlov

https://pypi.org/project/polyglot/

http://www.pullenti.ru/

## Natasha

In [30]:
from natasha import (
    Segmenter,
    NewsEmbedding,
    NewsNERTagger,
    Doc
)
	

text = '''
Иисус ходил по воде. Простите, еще несколько цитат из приговора. «…Отрицал существование
Иисуса и пророка Мухаммеда», «наделял Иисуса Христа качествами
ожившего мертвеца — зомби» [и] «качествами покемонов —
представителей бестиария японской мифологии, тем самым совершил
преступление, предусмотренное статьей 148 УК РФ
'''

emb = NewsEmbedding()
segmenter = Segmenter()
ner_tagger = NewsNERTagger(emb)

doc = Doc(text)
doc.segment(segmenter)
doc.tag_ner(ner_tagger)
doc.ner.print()
for span in doc.spans:
    print(span)

Иисус ходил по воде. Простите, еще несколько цитат из приговора. 
PER──                                                            
«…Отрицал существование
Иисуса и пророка Мухаммеда», «наделял Иисуса Христа качествами
                                      PER──────────           
ожившего мертвеца — зомби» [и] «качествами покемонов —
представителей бестиария японской мифологии, тем самым совершил
преступление, предусмотренное статьей 148 УК РФ
                                             LO
DocSpan(start=1, stop=6, type='PER', text='Иисус', tokens=[...])
DocSpan(start=128, stop=141, type='PER', text='Иисуса Христа', tokens=[...])
DocSpan(start=317, stop=319, type='LOC', text='РФ', tokens=[...])


In [31]:
def calc_metrics_spans_only(true_spans, predicted_spans):
    exact, partial, missing = compare_span_sets(true_spans, predicted_spans)
    _, _, spurius = compare_span_sets(predicted_spans, true_spans)
    return exact, partial, missing, spurius

In [32]:
aexact = 0
apartial = 0
amissing = 0
aspurius = 0
for sample in test:
    true_spans = sample.spans
    doc = Doc(sample.text)
    doc.segment(segmenter)
    doc.tag_ner(ner_tagger)
    predicted_spans = [(span.start, span.stop, span.type) for span in doc.spans if span.type == "PER"]
    exact, partial, missing, spurius = calc_metrics_spans_only(true_spans, predicted_spans)
    aexact += exact
    apartial += partial
    amissing += missing
    aspurius += spurius
print("Exact: {}, partial: {}, missing: {}, spurius: {}".format(aexact, apartial, amissing, aspurius))

Exact: 1414, partial: 7, missing: 44, spurius: 21
